# This is my sample .ipynb file!
This could be your analyses files, your visualization files, etc.

In [1]:
import matplotlib.pyplot as plt
import pandas as pd
from df_after_transform import df_after_transform
from sklearn import set_config
from sklearn.calibration import CalibrationDisplay
from sklearn.compose import (
    ColumnTransformer,
    make_column_selector,
    make_column_transformer,
)
from sklearn.impute import SimpleImputer
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import (
    ConfusionMatrixDisplay,
    DetCurveDisplay,
    PrecisionRecallDisplay,
    RocCurveDisplay,
    classification_report,
)
from sklearn.model_selection import (
    GridSearchCV,
    KFold,
    cross_validate,
    train_test_split,
)
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import OneHotEncoder, StandardScaler

set_config(display="diagram")  # display='text' is the default

pd.set_option(
    "display.max_colwidth", 1000, "display.max_rows", 50, "display.max_columns", None
)

In [2]:
import pandas as pd

sample=pd.read_csv('IMPORTANT.csv')

In [3]:
sample

Firm              Unnamed: 1 ticker
0             Opendoor           Opendoor Inc.   OPEN
1            Medtronic          Medtronic Inc.    MDT
2               Redfin             Redfin Inc.   RDFN
3               Acxiom             Acxiom Inc.    NaN
4    Pear Therapeutics  Pear Therapeutics Inc.   PEAR
..                 ...                     ...    ...
257              GoPro              GoPro Inc.   GPRO
258               Domo               Domo Inc.   DOMO
259  Sage Therapeutics  Sage Therapeutics Inc.   SAGE
260              Maven              Maven Inc.    NaN
261          Blackbaud          Blackbaud Inc.   BLKB

[262 rows x 3 columns]

In [4]:
import pandas_datareader as pdr
from datetime import datetime
import yfinance as yf

stocks = [str(ticker) for ticker in sample['ticker'].tolist()]  # convert tickers to strings
start = datetime(2020, 1, 1)
end = datetime(2023, 4, 1)

# load
stock_prices = yf.download(stocks, start, end)

[*********************100%***********************]  250 of 250 completed

2 Failed downloads:
- SMFR: No timezone found, symbol may be delisted
- ZY: No timezone found, symbol may be delisted


In [5]:
stock_prices

Adj Close                                                    
                  AAPL        ABNB   ABSI   ACCD        ADBE       ADPT   
Date                                                                      
2020-01-02   73.449394         NaN    NaN    NaN  334.429993  29.370001  \
2020-01-03   72.735321         NaN    NaN    NaN  331.809998  29.799999   
2020-01-06   73.314888         NaN    NaN    NaN  333.709991  29.600000   
2020-01-07   72.970085         NaN    NaN    NaN  333.390015  29.639999   
2020-01-08   74.143883         NaN    NaN    NaN  337.869995  29.990000   
...                ...         ...    ...    ...         ...        ...   
2023-03-27  158.279999  117.910004  1.730  13.30  373.149994   8.720000   
2023-03-28  157.649994  116.610001  1.630  13.06  373.399994   8.240000   
2023-03-29  160.770004  118.800003  1.765  13.37  379.160004   8.440000   
2023-03-30  162.360001  122.279999  1.680  13.57  381.899994   8.420000   
2023-03-31  164.899994  124.400002  1.750  14.38  385.369995   8.830000   

                                                                       
                  ADSK   AFRM   AMPL        AMZN  APGT    APP   APRN   
Date                                                                   
2020-01-02  187.830002    NaN    NaN   94.900497   NaN    NaN  6.360  \
2020-01-03  184.949997    NaN    NaN   93.748497   NaN    NaN  6.160   
2020-01-06  187.119995    NaN    NaN   95.143997   NaN    NaN  6.090   
2020-01-07  187.500000    NaN    NaN   95.343002   NaN    NaN  5.950   
2020-01-08  189.949997    NaN    NaN   94.598503   NaN    NaN  5.740   
...                ...    ...    ...         ...   ...    ...    ...   
2023-03-27  198.750000  10.22  11.66   98.040001  1.70  14.15  0.726   
2023-03-28  197.270004   9.47  11.54   97.239998  1.85  13.97  0.711   
2023-03-29  199.160004  10.50  11.79  100.250000  1.50  14.98  0.724   
2023-03-30  201.610001  10.42  11.87  102.000000  1.50  15.00  0.711   
2023-03-31  208.160004  11.27  12.44  103.290001  1.50  15.75  0.678   

                                                                              
                 ASAN   ASTR       BALY  BARK  BBAI  BFLY  BIGC  BIRD  BKKT   
Date                                                                          
2020-01-02        NaN    NaN  25.179483   NaN   NaN   NaN   NaN   NaN   NaN  \
2020-01-03        NaN    NaN  25.089842   NaN   NaN   NaN   NaN   NaN   NaN   
2020-01-06        NaN    NaN  25.727295   NaN   NaN   NaN   NaN   NaN   NaN   
2020-01-07        NaN    NaN  25.617733   NaN   NaN   NaN   NaN   NaN   NaN   
2020-01-08        NaN    NaN  25.896620   NaN   NaN   NaN   NaN   NaN   NaN   
...               ...    ...        ...   ...   ...   ...   ...   ...   ...   
2023-03-27  20.040001  0.416  18.150000  1.23  1.96  1.87  8.53  1.23  1.49   
2023-03-28  19.450001  0.416  18.020000  1.34  1.88  1.77  8.38  1.26  1.46   
2023-03-29  20.020000  0.432  19.010000  1.40  2.02  1.65  8.55  1.25  1.57   
2023-03-30  20.049999  0.485  19.020000  1.42  1.98  1.64  8.52  1.19  1.64   
2023-03-31  21.129999  0.425  19.520000  1.45  2.44  1.88  8.94  1.20  1.72   

                                                                            
             BLI       BLKB   BLND       BMRN   BMTX  BOXDQ   BRDS   BTTX   
Date                                                                        
2020-01-02   NaN  80.756813    NaN  84.040001  10.27    NaN    NaN    NaN  \
2020-01-03   NaN  78.620338    NaN  84.000000  10.25    NaN    NaN    NaN   
2020-01-06   NaN  79.269264    NaN  84.589996  10.26    NaN    NaN    NaN   
2020-01-07   NaN  77.711830    NaN  84.209999  10.27    NaN    NaN    NaN   
2020-01-08   NaN  77.981392    NaN  84.709999  10.27    NaN    NaN    NaN   
...          ...        ...    ...        ...    ...    ...    ...    ...   
2023-03-27  1.12  63.930000  0.880  91.500000   3.85  0.203  0.136  0.821   
2023-03-28  1.05  64.879997  0.886  91.440002   3.34  0.171  0.194  0.698   

In [6]:
stock_prices1 = stock_prices.transpose()
stock_prices1.index.names=["stock_info","ticker"]
stock_prices1.columns.names=["date"]
# 打印出前几行数据来检查 DataFrame 是否已经转置成功
stock_prices1.head()

date               2020-01-02 00:00:00  2020-01-03 00:00:00   
stock_info ticker                                             
Adj Close  AAPL              73.449394            72.735321  \
           ABNB                    NaN                  NaN   
           ABSI                    NaN                  NaN   
           ACCD                    NaN                  NaN   
           ADBE             334.429993           331.809998   

date               2020-01-06 00:00:00  2020-01-07 00:00:00   
stock_info ticker                                             
Adj Close  AAPL              73.314888            72.970085  \
           ABNB                    NaN                  NaN   
           ABSI                    NaN                  NaN   
           ACCD                    NaN                  NaN   
           ADBE             333.709991           333.390015   

date               2020-01-08 00:00:00  2020-01-09 00:00:00   
stock_info ticker                                             
Adj Close  AAPL              74.143883            75.718765  \
           ABNB                    NaN                  NaN   
           ABSI                    NaN                  NaN   
           ACCD                    NaN                  NaN   
           ADBE             337.869995           340.450012   

date               2020-01-10 00:00:00  2020-01-13 00:00:00   
stock_info ticker                                             
Adj Close  AAPL              75.889954            77.511292  \
           ABNB                    NaN                  NaN   
           ABSI                    NaN                  NaN   
           ACCD                    NaN                  NaN   
           ADBE             339.809998           345.630005   

date               2020-01-14 00:00:00  2020-01-15 00:00:00   
stock_info ticker                                             
Adj Close  AAPL              76.464638            76.136948  \
           ABNB                    NaN                  NaN   
           ABSI                    NaN                  NaN   
           ACCD                    NaN                  NaN   
           ADBE             344.630005           342.940002   

date               2020-01-16 00:00:00  2020-01-17 00:00:00   
stock_info ticker                                             
Adj Close  AAPL              77.090675            77.944145  \
           ABNB                    NaN                  NaN   
           ABSI                    NaN                  NaN   
           ACCD                    NaN                  NaN   
           ADBE             345.380005           349.739990   

date               2020-01-21 00:00:00  2020-01-22 00:00:00   
stock_info ticker                                             
Adj Close  AAPL              77.415932            77.692276  \
           ABNB                    NaN                  NaN   
           ABSI                    NaN                  NaN   
           ACCD                    NaN                  NaN   
           ADBE             350.000000           350.059998   

date               2020-01-23 00:00:00  2020-01-24 00:00:00   
stock_info ticker                                             
Adj Close  AAPL              78.066422            77.841438  \
           ABNB                    NaN                  NaN   
           ABSI                    NaN                  NaN   
           ACCD                    NaN                  NaN   
           ADBE             351.760010           351.369995   

date               2020-01-27 00:00:00  2020-01-28 00:00:00   
stock_info ticker                                             
Adj Close  AAPL              75.552483            77.689812  \
           ABNB                    NaN                  NaN   
           ABSI                    NaN                  NaN   
           ACCD                    NaN                  NaN   
           ADBE             346.899994           354.630005   

date               202

In [7]:
stock_prices1=stock_prices1[:249]

In [8]:
stock_prices1

date               2020-01-02 00:00:00  2020-01-03 00:00:00   
stock_info ticker                                             
Adj Close  AAPL              73.449394            72.735321  \
           ABNB                    NaN                  NaN   
           ABSI                    NaN                  NaN   
           ACCD                    NaN                  NaN   
           ADBE             334.429993           331.809998   
...                                ...                  ...   
           YEXT              14.640000            14.250000   
           Z                 45.209999            44.720001   
           ZM                68.720001            67.279999   
           ZS                47.330002            47.380001   
           ZUO               14.760000            14.770000   

date               2020-01-06 00:00:00  2020-01-07 00:00:00   
stock_info ticker                                             
Adj Close  AAPL              73.314888            72.970085  \
           ABNB                    NaN                  NaN   
           ABSI                    NaN                  NaN   
           ACCD                    NaN                  NaN   
           ADBE             333.709991           333.390015   
...                                ...                  ...   
           YEXT              14.770000            14.710000   
           Z                 44.639999            45.770000   
           ZM                70.320000            71.900002   
           ZS                48.700001            48.400002   
           ZUO               14.670000            14.690000   

date               2020-01-08 00:00:00  2020-01-09 00:00:00   
stock_info ticker                                             
Adj Close  AAPL              74.143883            75.718765  \
           ABNB                    NaN                  NaN   
           ABSI                    NaN                  NaN   
           ACCD                    NaN                  NaN   
           ADBE             337.869995           340.450012   
...                                ...                  ...   
           YEXT              14.770000            14.950000   
           Z                 45.770000            45.779999   
           ZM                72.550003            72.620003   
           ZS                50.750000            54.000000   
           ZUO               14.660000            14.880000   

date               2020-01-10 00:00:00  2020-01-13 00:00:00   
stock_info ticker                                             
Adj Close  AAPL              75.889954            77.511292  \
           ABNB                    NaN                  NaN   
           ABSI                    NaN                  NaN   
           ACCD                    NaN                  NaN   
           ADBE             339.809998           345.630005   
...                                ...                  ...   
           YEXT              14.950000            15.590000   
           Z                 45.590000            46.580002   
           ZM                73.089996            74.029999   
           ZS                55.000000            59.619999   
           ZUO               15.030000            15.450000   

date               2020-01-14 00:00:00  2020-01-15 00:00:00   
stock_info ticker                                             
Adj Close  AAPL              76.464638            76.136948  \
           ABNB                    NaN                  NaN   
           ABSI                    NaN                  NaN   
           ACCD                    NaN                  NaN   
           ADBE             344.630005           342.940002   
...                                ...                  ...   
           YEXT              15.340000            15.140000   
           Z                 47.070000            46.680000   
           ZM                73.160004            76.940002   
           ZS              

In [9]:
stock_prices1 = stock_prices1.reset_index()

# 打印出前几行数据来检查 DataFrame 是否已经重置成功
stock_prices1.head()


date stock_info ticker  2020-01-02 00:00:00  2020-01-03 00:00:00   
0     Adj Close   AAPL            73.449394            72.735321  \
1     Adj Close   ABNB                  NaN                  NaN   
2     Adj Close   ABSI                  NaN                  NaN   
3     Adj Close   ACCD                  NaN                  NaN   
4     Adj Close   ADBE           334.429993           331.809998   

date  2020-01-06 00:00:00  2020-01-07 00:00:00  2020-01-08 00:00:00   
0               73.314888            72.970085            74.143883  \
1                     NaN                  NaN                  NaN   
2                     NaN                  NaN                  NaN   
3                     NaN                  NaN                  NaN   
4              333.709991           333.390015           337.869995   

date  2020-01-09 00:00:00  2020-01-10 00:00:00  2020-01-13 00:00:00   
0               75.718765            75.889954            77.511292  \
1                     NaN                  NaN                  NaN   
2                     NaN                  NaN                  NaN   
3                     NaN                  NaN                  NaN   
4              340.450012           339.809998           345.630005   

date  2020-01-14 00:00:00  2020-01-15 00:00:00  2020-01-16 00:00:00   
0               76.464638            76.136948            77.090675  \
1                     NaN                  NaN                  NaN   
2                     NaN                  NaN                  NaN   
3                     NaN                  NaN                  NaN   
4              344.630005           342.940002           345.380005   

date  2020-01-17 00:00:00  2020-01-21 00:00:00  2020-01-22 00:00:00   
0               77.944145            77.415932            77.692276  \
1                     NaN                  NaN                  NaN   
2                     NaN                  NaN                  NaN   
3                     NaN                  NaN                  NaN   
4              349.739990           350.000000           350.059998   

date  2020-01-23 00:00:00  2020-01-24 00:00:00  2020-01-27 00:00:00   
0               78.066422            77.841438            75.552483  \
1                     NaN                  NaN                  NaN   
2                     NaN                  NaN                  NaN   
3                     NaN                  NaN                  NaN   
4              351.760010           351.369995           346.899994   

date  2020-01-28 00:00:00  2020-01-29 00:00:00  2020-01-30 00:00:00   
0               77.689812            79.316032            79.201111  \
1                     NaN                  NaN                  NaN   
2                     NaN                  NaN                  NaN   
3                     NaN                  NaN                  NaN   
4              354.630005           351.660004           356.739990   

date  2020-01-31 00:00:00  2020-02-03 00:00:00  2020-02-04 00:00:00   
0               75.689445            75.481567            77.973503  \
1                     NaN                  NaN                  NaN   
2                     NaN                  NaN                  NaN   
3                     NaN                  NaN                  NaN   
4              351.140015           358.000000           366.739990   

date  2020-02-05 00:00:00  2020-02-06 00:00:00  2020-02-07 00:00:00   
0               78.609314            79.528793            78.447792  \
1                     NaN                  NaN                  NaN   
2                     NaN                  NaN                  NaN   
3                     NaN                  NaN                  NaN   
4              365.549988           367.459991           366.089996   

date  2020-02-10 00:00:00  2020-02-11 00:00:00  2020-02-12 00:00:00   
0               78.820389            78.344818            80.205360  \
1                     NaN        

In [10]:
stock_prices1=stock_prices1.drop(["stock_info"], axis=1)

# 打印出前几行数据来检查 DataFrame 是否已经更新成功
stock_prices1

date ticker  2020-01-02 00:00:00  2020-01-03 00:00:00  2020-01-06 00:00:00   
0      AAPL            73.449394            72.735321            73.314888  \
1      ABNB                  NaN                  NaN                  NaN   
2      ABSI                  NaN                  NaN                  NaN   
3      ACCD                  NaN                  NaN                  NaN   
4      ADBE           334.429993           331.809998           333.709991   
..      ...                  ...                  ...                  ...   
244    YEXT            14.640000            14.250000            14.770000   
245       Z            45.209999            44.720001            44.639999   
246      ZM            68.720001            67.279999            70.320000   
247      ZS            47.330002            47.380001            48.700001   
248     ZUO            14.760000            14.770000            14.670000   

date  2020-01-07 00:00:00  2020-01-08 00:00:00  2020-01-09 00:00:00   
0               72.970085            74.143883            75.718765  \
1                     NaN                  NaN                  NaN   
2                     NaN                  NaN                  NaN   
3                     NaN                  NaN                  NaN   
4              333.390015           337.869995           340.450012   
..                    ...                  ...                  ...   
244             14.710000            14.770000            14.950000   
245             45.770000            45.770000            45.779999   
246             71.900002            72.550003            72.620003   
247             48.400002            50.750000            54.000000   
248             14.690000            14.660000            14.880000   

date  2020-01-10 00:00:00  2020-01-13 00:00:00  2020-01-14 00:00:00   
0               75.889954            77.511292            76.464638  \
1                     NaN                  NaN                  NaN   
2                     NaN                  NaN                  NaN   
3                     NaN                  NaN                  NaN   
4              339.809998           345.630005           344.630005   
..                    ...                  ...                  ...   
244             14.950000            15.590000            15.340000   
245             45.590000            46.580002            47.070000   
246             73.089996            74.029999            73.160004   
247             55.000000            59.619999            59.540001   
248             15.030000            15.450000            15.340000   

date  2020-01-15 00:00:00  2020-01-16 00:00:00  2020-01-17 00:00:00   
0               76.136948            77.090675            77.944145  \
1                     NaN                  NaN                  NaN   
2                     NaN                  NaN                  NaN   
3                     NaN                  NaN                  NaN   
4              342.940002           345.380005           349.739990   
..                    ...                  ...                  ...   
244             15.140000            15.350000            15.630000   
245             46.680000            47.180000            47.959999   
246             76.940002            76.110001            75.559998   
247             59.990002            61.820000            59.430000   
248             15.500000            15.660000            15.350000   

date  2020-01-21 00:00:00  2020-01-22 00:00:00  2020-01-23 00:00:00   
0               77.415932            77.692276            78.066422  \
1                     NaN                  NaN                  NaN   
2                     NaN                  NaN                  NaN   
3                     NaN                  NaN                  NaN   
4              350.000000           350.059998           351.760010   
..                    ...                  ...                  ...   
244    

In [11]:
stock_prices1.rename(columns={"date": "index"}, inplace=True)
stock_prices1

date ticker  2020-01-02 00:00:00  2020-01-03 00:00:00  2020-01-06 00:00:00   
0      AAPL            73.449394            72.735321            73.314888  \
1      ABNB                  NaN                  NaN                  NaN   
2      ABSI                  NaN                  NaN                  NaN   
3      ACCD                  NaN                  NaN                  NaN   
4      ADBE           334.429993           331.809998           333.709991   
..      ...                  ...                  ...                  ...   
244    YEXT            14.640000            14.250000            14.770000   
245       Z            45.209999            44.720001            44.639999   
246      ZM            68.720001            67.279999            70.320000   
247      ZS            47.330002            47.380001            48.700001   
248     ZUO            14.760000            14.770000            14.670000   

date  2020-01-07 00:00:00  2020-01-08 00:00:00  2020-01-09 00:00:00   
0               72.970085            74.143883            75.718765  \
1                     NaN                  NaN                  NaN   
2                     NaN                  NaN                  NaN   
3                     NaN                  NaN                  NaN   
4              333.390015           337.869995           340.450012   
..                    ...                  ...                  ...   
244             14.710000            14.770000            14.950000   
245             45.770000            45.770000            45.779999   
246             71.900002            72.550003            72.620003   
247             48.400002            50.750000            54.000000   
248             14.690000            14.660000            14.880000   

date  2020-01-10 00:00:00  2020-01-13 00:00:00  2020-01-14 00:00:00   
0               75.889954            77.511292            76.464638  \
1                     NaN                  NaN                  NaN   
2                     NaN                  NaN                  NaN   
3                     NaN                  NaN                  NaN   
4              339.809998           345.630005           344.630005   
..                    ...                  ...                  ...   
244             14.950000            15.590000            15.340000   
245             45.590000            46.580002            47.070000   
246             73.089996            74.029999            73.160004   
247             55.000000            59.619999            59.540001   
248             15.030000            15.450000            15.340000   

date  2020-01-15 00:00:00  2020-01-16 00:00:00  2020-01-17 00:00:00   
0               76.136948            77.090675            77.944145  \
1                     NaN                  NaN                  NaN   
2                     NaN                  NaN                  NaN   
3                     NaN                  NaN                  NaN   
4              342.940002           345.380005           349.739990   
..                    ...                  ...                  ...   
244             15.140000            15.350000            15.630000   
245             46.680000            47.180000            47.959999   
246             76.940002            76.110001            75.559998   
247             59.990002            61.820000            59.430000   
248             15.500000            15.660000            15.350000   

date  2020-01-21 00:00:00  2020-01-22 00:00:00  2020-01-23 00:00:00   
0               77.415932            77.692276            78.066422  \
1                     NaN                  NaN                  NaN   
2                     NaN                  NaN                  NaN   
3                     NaN                  NaN                  NaN   
4              350.000000           350.059998           351.760010   
..                    ...                  ...                  ...   
244    

In [12]:
sample=sample.drop(['Unnamed: 1'], axis=1)

sample

Firm ticker
0             Opendoor   OPEN
1            Medtronic    MDT
2               Redfin   RDFN
3               Acxiom    NaN
4    Pear Therapeutics   PEAR
..                 ...    ...
257              GoPro   GPRO
258               Domo   DOMO
259  Sage Therapeutics   SAGE
260              Maven    NaN
261          Blackbaud   BLKB

[262 rows x 2 columns]

In [13]:
new=sample.merge(stock_prices1, on='ticker')
new

Firm ticker  2020-01-02 00:00:00  2020-01-03 00:00:00   
0              Opendoor   OPEN                  NaN                  NaN  \
1             Medtronic    MDT           105.364601           104.739204   
2                Redfin   RDFN            21.625000            21.610001   
3     Pear Therapeutics   PEAR                  NaN                  NaN   
4    Pear Therapeutics    PEAR                  NaN                  NaN   
..                  ...    ...                  ...                  ...   
244            CarGurus   CARG            36.509998            36.349998   
245               GoPro   GPRO             4.400000             4.320000   
246                Domo   DOMO            21.040001            21.500000   
247   Sage Therapeutics   SAGE            73.160004            73.529999   
248           Blackbaud   BLKB            80.756813            78.620338   

     2020-01-06 00:00:00  2020-01-07 00:00:00  2020-01-08 00:00:00   
0                    NaN                  NaN                  NaN  \
1             105.668114           105.300240           107.148888   
2              21.410000            21.469999            21.459999   
3                    NaN                  NaN                  NaN   
4                    NaN                  NaN                  NaN   
..                   ...                  ...                  ...   
244            36.380001            36.189999            36.430000   
245             4.470000             4.400000             4.420000   
246            22.690001            22.650000            22.610001   
247            75.400002            74.820000            75.639999   
248            79.269264            77.711830            77.981392   

     2020-01-09 00:00:00  2020-01-10 00:00:00  2020-01-13 00:00:00   
0                    NaN                  NaN                  NaN  \
1             108.887184           109.117126           108.537697   
2              21.709999            21.850000            22.250000   
3                    NaN                  NaN                  NaN   
4                    NaN                  NaN                  NaN   
..                   ...                  ...                  ...   
244            35.290001            35.180000            34.869999   
245             4.420000             4.270000             4.260000   
246            23.650000            24.190001            24.559999   
247            76.120003            77.239998            74.769997   
248            79.209358            78.580399            80.427353   

     2020-01-14 00:00:00  2020-01-15 00:00:00  2020-01-16 00:00:00   
0                    NaN                  NaN                  NaN  \
1             107.645546           107.912277           109.319466   
2              22.360001            23.950001            24.219999   
3                    NaN                  NaN                  NaN   
4                    NaN                  NaN                  NaN   
..                   ...                  ...                  ...   
244            35.450001            36.009998            37.730000   
245             4.150000             4.240000             4.310000   
246            24.290001            24.910000            24.969999   
247            76.680000            74.910004            74.089996   
248            79.878265            79.828346            81.954834   

     2020-01-17 00:00:00  2020-01-21 00:00:00  2020-01-22 00:00:00   
0                    NaN                  NaN                  NaN  \
1             109.475815           110.662262           111.370453   
2              23.520000            24.049999            24.490000   
3                    NaN                  NaN                  NaN   
4                    NaN                  NaN                  NaN   
..                   ...                  ...                  ...   
244            38.060001            37.970001            37.000000   
245             4.29000

In [14]:
layoff=pd.read_csv('layoffs_data.csv')

layoff

Company     Location_HQ        Industry  Laid_Off_Count   
0             Opendoor     SF Bay Area     Real Estate           560.0  \
1          Culture Amp       Melbourne              HR             NaN   
2                 Noon          Riyadh          Retail             NaN   
3     Ten Square Games         Wrocław        Consumer           120.0   
4               Ynsect           Paris            Food            17.0   
...                ...             ...             ...             ...   
2503      HopSkipDrive     Los Angeles  Transportation             8.0   
2504       Panda Squad     SF Bay Area        Consumer             6.0   
2505     Tamara Mellon     Los Angeles          Retail            20.0   
2506          EasyPost  Salt Lake City       Logistics            75.0   
2507         Blackbaud      Charleston           Other           500.0   

      Percentage        Date   
0           0.22  2023-04-18  \
1           0.09  2023-04-18   
2           0.10  2023-04-18   
3           0.25  2023-04-17   
4           0.25  2023-04-17   
...          ...         ...   
2503        0.10  2020-03-13   
2504        0.75  2020-03-13   
2505        0.40  2020-03-12   
2506         NaN  2020-03-11   
2507        0.14         NaN   

                                                                                                                                                           Source   
0                                                                 https://www.inman.com/2023/04/18/opendoor-lays-off-22-of-its-workforce-in-latest-round-of-cuts/  \
1                                                          https://www.cultureamp.com/company/announcements/note-to-culture-amp-employees-from-ceo-didier-elzinga   
2                                                                                          https://yourstory.com/ys-gulf/noon-lays-off-10-percent-dubai-workforce   
3                https://economictimes.indiatimes.com/tech/technology/ten-square-games-to-lay-off-25-of-staff-suspend-two-major-projects/articleshow/99558794.cms   
4                                                                                               https://pitchbook.com/news/articles/agtech-ynsect-funding-layoffs   
...                                                                                                                                                           ...   
2503                                                                      https://layoffs.fyi/2020/04/02/hopskipdrive-laid-off-10-of-team-due-to-school-closures/   
2504                                                                                                  https://twitter.com/danielsinger/status/1238545571092160514   
2505                                                                                                                      https://layoffs.fyi/list/tamara-mellon/   
2506                                                    https://www.bizjournals.com/louisville/news/2020/03/11/logistics-company-ceasing-operations-planning.html   
2507  https://www.postandcourier.com/business/sc-tech-employer-blackbaud-has-cut-about-500-jobs-since-last-year/article_ef9dd60a-ac9b-11ed-8c4a-bbbeb9f0cda5.html   

      Funds_Raised     Stage           Date_Added        Country   
0           1900.0  Post-IPO  2023-04-18 17:55:14  United States  \
1            257.0  Series F  2023-04-19 00:21:55      Australia   
2              NaN   Unknown  2023-04-19 00:23:39   Saudi Arabia   
3              NaN      Seed  2023-04-18 04:44:03         Poland   
4            579.0  Series D  2023-04-18 04:45:17         France   
...            ...       ...                  ...            ...   
2503          45.0   Unknown  2020-04-03 04:47:03  United States   
2504           1.0      Seed  2020-04-17 00:12:49  United States   
2505          90.0  Series C  2020-03-31 16:04:23  United States   
2506          12.0  Series A  2020-03-31 13:21:54  United States   
2507        

In [15]:
newdata=layoff.merge(new, left_on='Company', right_on='Firm')
newdata

Company     Location_HQ        Industry  Laid_Off_Count   
0             Opendoor     SF Bay Area     Real Estate           560.0  \
1             Opendoor     SF Bay Area     Real Estate           550.0   
2             Opendoor     SF Bay Area     Real Estate           600.0   
3            Medtronic     SF Bay Area      Healthcare            59.0   
4               Redfin         Seattle     Real Estate           201.0   
..                 ...             ...             ...             ...   
369           CarGurus          Boston  Transportation           130.0   
370              GoPro     SF Bay Area        Consumer           200.0   
371               Domo  Salt Lake City            Data            90.0   
372  Sage Therapeutics          Boston      Healthcare           340.0   
373          Blackbaud      Charleston           Other           500.0   

     Percentage        Date   
0          0.22  2023-04-18  \
1          0.18  2022-11-02   
2          0.35  2020-04-15   
3           NaN  2023-04-12   
4          0.04  2023-04-11   
..          ...         ...   
369        0.13  2020-04-16   
370        0.20  2020-04-15   
371        0.10  2020-04-09   
372        0.53  2020-04-07   
373        0.14         NaN   

                                                                                                                                                          Source   
0                                                                https://www.inman.com/2023/04/18/opendoor-lays-off-22-of-its-workforce-in-latest-round-of-cuts/  \
1                                                 https://www.bloomberg.com/news/articles/2022-11-02/opendoor-lays-off-18-of-workers-in-wave-of-housing-cutbacks   
2                                                               https://layoffs.fyi/2020/04/16/opendoor-lays-off-600-people-amid-declining-real-estate-activity/   
3                                                                                                       https://www.massdevice.com/medtronic-layoffs-california/   
4                                                           https://www.geekwire.com/2023/redfin-lays-off-201-employees-as-housing-market-continues-to-retrench/   
..                                                                                                                                                           ...   
369                                                                                              https://layoffs.fyi/2020/05/04/cargurus-laid-off-130-employees/   
370                                                               https://techcrunch.com/2020/04/16/gopro-lays-off-200-employees-representing-20-of-the-company/   
371                                        https://www.ksl.com/article/46740514/domo-forced-to-lay-off-10-of-workforce-due-to-economic-impact-caused-by-covid-19   
372                                                                          https://www.biopharmadive.com/news/sage-restructuring-layoffs-340-employees/575641/   
373  https://www.postandcourier.com/business/sc-tech-employer-blackbaud-has-cut-about-500-jobs-since-last-year/article_ef9dd60a-ac9b-11ed-8c4a-bbbeb9f0cda5.html   

     Funds_Raised     Stage           Date_Added        Country   
0          1900.0  Post-IPO  2023-04-18 17:55:14  United States  \
1          1900.0  Post-IPO  2022-11-02 17:07:34  United States   
2          1500.0  Series E  2020-04-15 19:27:35  United States   
3          5900.0  Post-IPO  2023-04-14 03:06:16  United States   
4           320.0  Post-IPO  2023-04-14 02:59:09  United States   
..            ...       ...                  ...            ...   
369           1.0  Post-IPO  2020-04-16 23:46:47  United States   
370         288.0  Post-IPO  2020-04-15 23:42:26  United States   
371         689.0  Post-IPO  2020-04-11 04:56:24  United States   
372         438.0  Post-IPO  2020-04-08 22:22:07  United States   
373           NaN  Post-IPO  2023-02-15 19:06:4

In [16]:
>>> from pathlib import Path  
>>> filepath = Path('newdata.csv')  
>>> filepath.parent.mkdir(parents=True, exist_ok=True)  
>>> newdata.to_csv(filepath)  